In [1]:
from sagemaker.huggingface.model import HuggingFaceModel
import sagemaker
import os
from dotenv import load_dotenv
load_dotenv()

sagemaker.config INFO - Not applying SDK defaults from location: /Library/Application Support/sagemaker/config.yaml
sagemaker.config INFO - Not applying SDK defaults from location: /Users/abhijitdeshpande/Library/Application Support/sagemaker/config.yaml


True

In [2]:
import os

# Remove proxy vars if not needed
os.environ.pop("HTTP_PROXY", None)
os.environ.pop("HTTPS_PROXY", None)

# Use the certifi-provided CA bundle
os.environ["AWS_CA_BUNDLE"] = "/Volumes/LaCie/Projects_portfolio/NLP/SupportIQ/venv/lib/python3.11/site-packages/certifi/cacert.pem"

# Test AWS call
import boto3
print(boto3.client('sts').get_caller_identity())

{'UserId': 'AIDA2PNZRCZDH2V4XL47W', 'Account': '720332985926', 'Arn': 'arn:aws:iam::720332985926:user/dev-user', 'ResponseMetadata': {'RequestId': 'ec276475-f282-4c52-a03b-e75953868c17', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'ec276475-f282-4c52-a03b-e75953868c17', 'content-type': 'text/xml', 'content-length': '405', 'date': 'Sun, 06 Jul 2025 15:28:49 GMT'}, 'RetryAttempts': 0}}


In [3]:
sagemaker_session = sagemaker.Session()

In [4]:
model_uri = 's3://sagemaker-us-east-1-720332985926/huggingface-pytorch-training-2025-07-05-23-42-49-059/output/model.tar.gz'

In [5]:
huggingface_model = HuggingFaceModel(
    entry_point='batch_transform.py',
    model_data=model_uri,
    source_dir=os.getenv("SOURCE_DIR"),
    role=os.getenv("ROLE"),
    transformers_version='4.49.0',
    py_version='py312',
    pytorch_version='2.6.0',
    sagemaker_session=sagemaker_session
    )

### sagemaker endpoint 
predictor = huggingface_model.deploy(
    initial_instance_count=1,
    instance_type='ml.g4dn.xlarge'
    )


In [ ]:
#predictor.predict({"inputs": "Classify the intent:  Can I cacnel my ticket?"})


In [6]:
transformer = huggingface_model.transformer(
    instance_count=1,
    instance_type='ml.g4dn.xlarge',
    strategy="SingleRecord",
    output_path='s3://sagemaker-us-east-1-720332985926/transformer/output/',
    accept="application/json",
    assemble_with="Line"
)

In [7]:
transformer.transform(
    data="s3://gen-ai-repository/finetuning/flan-t5/data/roberta-test.jsonl",
    content_type="application/json",
    split_type='Line',
    wait=True	
)

INFO:sagemaker:Creating transform job with name: huggingface-pytorch-inference-2025-07-06-15-48-27-419


............................................2025-07-06T15:56:00.367:[sagemaker logs]: MaxConcurrentTransforms=1, MaxPayloadInMB=6, BatchStrategy=SINGLE_RECORD
2025-07-06T15:55:59,998 [INFO ] main com.amazonaws.ml.mms.ModelServer - 
MMS Home: /opt/conda/lib/python3.12/site-packages
Current directory: /
Temp directory: /tmp
Number of GPUs: 1
Number of CPUs: 4
Max heap size: 3934 M
Python executable: /opt/conda/bin/python3.12
Config file: /etc/sagemaker-mms.properties
Inference address: http://0.0.0.0:8080
Management address: http://0.0.0.0:8080
Model Store: /
Initial Models: model=/opt/ml/model
Log dir: null
Metrics dir: null
Netty threads: 0
Netty client threads: 0
Default workers per model: 1
Blacklist Regex: N/A
Maximum Response Size: 6553500
Maximum Request Size: 6553500
Preload model: false
Prefer direct buffer: false
2025-07-06T15:56:00,005 [INFO ] main com.amazonaws.ml.mms.ModelServer - Loading initial models: /opt/ml/model preload_model: false
2025-07-06T15:56:00,052 [WARN ] W-90